In [1]:
from src.returns_analysis import analyse_returns_characteristics
from src.process_selection import process_selection, recommend_process
from src.var import produce_var_results
from src.chart_visual import chart_visuals
from src.processes import Processes
from src.get_data import HistoricalData
from src.util import parse_json
import plotly.graph_objects as go
import numpy as np
import pandas as pd
import datetime as dt

In [2]:
# config = parse_json("config.json")

# histdata = HistoricalData(config["binance"]["API_KEY"], config["binance"]["API_SECRET"])
# df = histdata.getKline("SOLUSDC","12h").dropna()
# histdata.save_data("test_data.csv")

In [3]:
df = pd.read_csv("test_data.csv").dropna()
df["opentime"] = pd.to_datetime(df.opentime)
df["closetime"] = pd.to_datetime(df.closetime)
df.head()

opentime    open    high     low   close   volume  \
1 2025-06-27 00:08:00  139.30  139.38  139.28  139.31  216.126   
2 2025-06-27 00:09:00  139.33  139.35  139.25  139.30   11.725   
3 2025-06-27 00:10:00  139.29  139.30  139.23  139.30   55.019   
4 2025-06-27 00:11:00  139.32  139.37  139.13  139.18  138.782   
5 2025-06-27 00:12:00  139.19  139.22  139.17  139.19   65.568   

                closetime     volume.1  log_returns  
1 2025-06-27 00:08:59.999  30115.31857    -0.000072  
2 2025-06-27 00:09:59.999   1633.54249    -0.000072  
3 2025-06-27 00:10:59.999   7662.20677     0.000000  
4 2025-06-27 00:11:59.999  19317.96890    -0.000862  
5 2025-06-27 00:12:59.999   9126.37733     0.000072

In [4]:
chart_visuals(df)

In [5]:
stats_summary, summary_table, sample_fig = analyse_returns_characteristics(df,False)

In [6]:
summary_table.show()
sample_fig.show()

In [7]:
test_results = process_selection(df)

In [8]:
recommend_process(test_results,stats_summary)

[{'process': 'GARCH',
  'confidence': 'high',
  'reason': 'significant volatility clustering detected'},
 {'process': 'jump diffusion (merton)',
  'confidence': 'medium',
  'reason': 'significant jump frequency'},
 {'process': 'Ornstein-Uhlenbeck',
  'confidence': 'medium',
  'reason': 'evidence of mean reversion in returns'},
 {'process': 'heston stochastic volatility',
  'confidence': 'medium',
  'reason': 'non-normal distrib with fat tails and skewness'}]

In [9]:
simulate_to = df.closetime.iloc[-1] + dt.timedelta(days = 5)
given_interval = ( df.closetime.iloc[1] - df.closetime.iloc[0] ).total_seconds()
periods = int((simulate_to - df.closetime.iloc[-1]).total_seconds() / given_interval)
processes = Processes(df,1234)

GBM

In [10]:
price_path = processes.gbm_price_path(periods,1_000)
produce_var_results(price_path,df)

Jump Diffusion Process

In [11]:
price_path = processes.jdp(periods,1_000)
produce_var_results(price_path,df)

OU Process

In [12]:
price_path = processes.ou(periods,1_000)
produce_var_results(price_path,df)

Fitted OU parameters: mu=3.20624132100886e-05, sigma=0.5104172777086196, theta=362.88


In [13]:
await processes.compare_processes(10,10)

Fitted OU parameters: mu=3.20624132100886e-05, sigma=0.5104172777086196, theta=362.88


GBM      JDP       OU
Max       $143.84  $144.38  $144.24
Min       $143.84  $143.21  $143.32
Mean      $143.84  $143.80  $143.69
Std         $0.00    $0.35    $0.27
Variance    $0.00    $0.12    $0.07